# Working with Data

In this notebook, we are going to work on the datasets that are going to be used in order to fine tune our NLP models.  
The different steps that we are going to follow are:

- Scraping ads data from Moroccan youtube products channels

# Scraping Data

In [39]:
from selenium import webdriver
from selenium.webdriver.edge.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
import time
import pandas as pd

In [52]:
def scrape_ads(url, channel_name, max_scroll=3, wait_time=2):
    options = Options()
    options.headless = True
    options.add_argument("--disable-gpu")
    options.add_argument("--no-sandbox")
    
    # Mute the audio
    options.add_argument("--mute-audio")

    driver = webdriver.Edge(options=options)

    driver.get(url)

    # Scroll down to load more videos
    height = driver.execute_script("return document.documentElement.scrollHeight")
    while True:
        driver.execute_script("window.scrollTo(0, document.documentElement.scrollHeight);")
        time.sleep(3)  # Allow time for the page to load
        new_height = driver.execute_script("return document.documentElement.scrollHeight")
        if new_height == height:
            time.sleep(5)  # Wait a bit longer to check if more content loads
            new_height = driver.execute_script("return document.documentElement.scrollHeight")
            if new_height == height:  # If the height is still the same, we are at the bottom
                break
        height = new_height

    src = driver.page_source
    soup = BeautifulSoup(src, 'lxml')
    video_links = soup.find_all('a', {'class': 'yt-simple-endpoint focus-on-expand style-scope ytd-rich-grid-media'})
    links = ["https://www.youtube.com" + link.get('href') for link in video_links if link.get('href')]

    ads = []
    titles = []
    for link in links:
        driver.get(link)
        time.sleep(5)

        src = driver.page_source
        soup = BeautifulSoup(src, 'lxml')

        ad_text_span = soup.find('span', class_='yt-core-attributed-string--link-inherit-color')
        ad_text = ad_text_span.text.strip() if ad_text_span else "No ad found"
        ads.append(ad_text)

        title_tag = soup.find('h1', {'class': 'title style-scope ytd-video-primary-info-renderer'})
        video_title = title_tag.text.strip() if title_tag else 'Title not found'
        titles.append(video_title)

    driver.quit()
    return ads, titles, links

In [63]:
channel = '@inwi'
url = f"https://www.youtube.com/{channel}/videos"
ads, titles, links = scrape_ads(url, channel)

C:\Users\ADS\AppData\Local\Temp\ipykernel_14604\116512856.py:3: DeprecationWarning: headless property is deprecated, instead use add_argument('--headless') or add_argument('--headless=new')
  options.headless = True


In [64]:
len(ads), len(titles), len(links)

(1380, 1380, 1380)

In [65]:
# put ads, titles and links in a dataframe
df3 = pd.DataFrame({'ad': ads, 'title': titles, 'link': links})

# add channel column
df3['channel'] = channel

In [67]:
df3.tail()

ad   
1375  initiative e-Madrassa proposée par inwi (Souti...  \
1376  initiative e-Madrassa proposée par inwi (Souti...   
1377   Le présent de l'indicatif des verbes pronominaux   
1378       Soutien scolaire - Français - Novembre 2012   
1379  Les contes marocains par la voix de Rachi El O...   

                                                  title   
1375  النشاط العلمي - حت التربة - الجزء الأول Janvie...  \
1376  اللغة العربية -أنشطة تطبيقية - الجزء الثاني - ...   
1377   Le présent de l'indicatif des verbes pronominaux   
1378       Soutien scolaire - Français - Novembre 2012   
1379  Emadrassa - L'espace de lecture présenté par R...   

                                             link channel  
1375  https://www.youtube.com/watch?v=9z2eSPv7dLo   @inwi  
1376  https://www.youtube.com/watch?v=IgsAKIPPjig   @inwi  
1377  https://www.youtube.com/watch?v=NvYs05Ix3OY   @inwi  
1378  https://www.youtube.com/watch?v=ThXZp-jRrUY   @inwi  
1379  https://www.youtube.com/watch?v=OPaECpKBl6I   @inwi

In [69]:
# concat df and df1 , df1, df3
df_ads = pd.concat([df, df1, df2, df3], ignore_index=True)

In [73]:
df_ads.head()

ad   
0  بشراكة مع بنك التغدية، مؤسسة أورنج تلتزم بالمس...  \
1  خدمة Transfert internet كاينة مع أورنج 🧡\n\nعن...   
2  أورنج ديما كاينة معاك !🧡\n\nمع خدمة solde dépa...   
3  لفراجة كاينة مع La Fibre d'Orange  !\nنتا غير ...   
4  سخاوة النجمة 3 المضوبلة كاينة ! 😍\nاستافدو من ...   

                                               title   
0                            Orange Maroc : خطوة خير  \
1                   Orange Maroc: Transfert de solde   
2                      Orange Maroc: Solde dépannage   
3  Orange Maroc : La Fibre d'Orange  لفراجة كاينة مع   
4             Orange Maroc : النجمة 3 المضوبلة كاينة   

                                          link       channel  
0  https://www.youtube.com/watch?v=3RoNBU-snrc  @orangemaroc  
1  https://www.youtube.com/watch?v=oQKRx9i2NdY  @orangemaroc  
2  https://www.youtube.com/watch?v=ElW8plKHRrI  @orangemaroc  
3  https://www.youtube.com/watch?v=sDt4tK29Vy8  @orangemaroc  
4  https://www.youtube.com/watch?v=U2VOn8mhN8U  @orangemaroc

In [72]:
df_ads.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3992 entries, 0 to 3991
Data columns (total 4 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   ad       3992 non-null   object
 1   title    3992 non-null   object
 2   link     3992 non-null   object
 3   channel  3992 non-null   object
dtypes: object(4)
memory usage: 124.9+ KB


In [70]:
# push to huggingface dataset
from datasets import Dataset

dataset = Dataset.from_pandas(df_ads)

In [49]:
from huggingface_hub import notebook_login
notebook_login()

In [71]:
# Push the dataset to your Hugging Face account
dataset.push_to_hub('MLINSEA/Moroccan_ads')

Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/4 [00:00<?, ?ba/s]

Deleting unused files from dataset repository:   0%|          | 0/1 [00:00<?, ?it/s]